In [1]:
from pprint import pprint

my_puzzle_input = 289326

class Spiral(object):
    def __init__(self, first, step):
        self.first = first + 1
        self.last = None
        self.step = step
        
    def __repr__(self):
        return str(self.first) + " - " + str(self.last)
        
i = 1
step = 2
side = 0

all_corners = []
all_spirals = []
corners = []

current_spiral = Spiral(i, step)

done = False
while not done:
    
    if side > 3:
        side = 0
        step += 2
        current_spiral.last = i
        all_spirals.append(current_spiral)
        all_corners.append(corners)
        corners = []
        current_spiral = Spiral(i, step)
        if i >= my_puzzle_input:
            done = True
        
    i += step
    side += 1
    
    corners.append(i)
    
#pprint(all_corners)
print(dir(current_spiral))
pprint(all_spirals)


['__class__', '__delattr__', '__dict__', '__dir__', '__doc__', '__eq__', '__format__', '__ge__', '__getattribute__', '__gt__', '__hash__', '__init__', '__init_subclass__', '__le__', '__lt__', '__module__', '__ne__', '__new__', '__reduce__', '__reduce_ex__', '__repr__', '__setattr__', '__sizeof__', '__str__', '__subclasshook__', '__weakref__', 'first', 'last', 'step']
[2 - 9,
 10 - 25,
 26 - 49,
 50 - 81,
 82 - 121,
 122 - 169,
 170 - 225,
 226 - 289,
 290 - 361,
 362 - 441,
 442 - 529,
 530 - 625,
 626 - 729,
 730 - 841,
 842 - 961,
 962 - 1089,
 1090 - 1225,
 1226 - 1369,
 1370 - 1521,
 1522 - 1681,
 1682 - 1849,
 1850 - 2025,
 2026 - 2209,
 2210 - 2401,
 2402 - 2601,
 2602 - 2809,
 2810 - 3025,
 3026 - 3249,
 3250 - 3481,
 3482 - 3721,
 3722 - 3969,
 3970 - 4225,
 4226 - 4489,
 4490 - 4761,
 4762 - 5041,
 5042 - 5329,
 5330 - 5625,
 5626 - 5929,
 5930 - 6241,
 6242 - 6561,
 6562 - 6889,
 6890 - 7225,
 7226 - 7569,
 7570 - 7921,
 7922 - 8281,
 8282 - 8649,
 8650 - 9025,
 9026 - 9409,


In [39]:
len(all_spirals)

269

## Part 2

As a stress test on the system, the programs here clear the grid and then store the value 1 in square 1. Then, in the same allocation order as shown above, they store the sum of the values in all adjacent squares, including diagonals.

So, the first few squares' values are chosen as follows:

* Square 1 starts with the value 1.
* Square 2 has only one adjacent filled square (with value 1), so it also stores 1.
* Square 3 has both of the above squares as neighbors and stores the sum of their values, 2.
* Square 4 has all three of the aforementioned squares as neighbors and stores the sum of their values, 4.
* Square 5 only has the first and fourth squares as neighbors, so it gets the value 5.

Once a square is written, its value does not change. Therefore, the first few squares would receive the following values:

    147  142  133  122   59
    304    5    4    2   57
    330   10    1    1   54
    351   11   23   25   26
    362  747  806--->   ...

What is the first value written that is larger than your puzzle input?

In [98]:
def grow(indices):
    return indices + [indices[-1]+1]

def proceed(indices):
    return indices[1:] + [indices[-1]+1]

def shrink(indices):
    return indices[1:]

def create_inner_indexer(length):
    yield grow
    while True:
        if length > 16:
            for n in range((length // 4) -4):
                yield proceed        
        yield shrink
        yield shrink
        yield grow
        yield grow
        
def find_inner_connecting_indices(length):
    if length == 8:
        return [[0]] * 8
    
    indexer_generator = create_inner_indexer(length)
    indices = [length - 8 - 1, 0]
    
    all_indices = []
    while length > 0:
        all_indices.append(indices)
        indexer = next(indexer_generator)
        indices = indexer(indices)
        length -= 1
    return all_indices
    
from pprint import pprint
#pprint(find_inner_connecting_indices(8))
#pprint(find_inner_connecting_indices(16))
pprint(find_inner_connecting_indices(32))

[[23, 0],
 [23, 0, 1],
 [0, 1, 2],
 [1, 2, 3],
 [2, 3, 4],
 [3, 4, 5],
 [4, 5],
 [5],
 [5, 6],
 [5, 6, 7],
 [6, 7, 8],
 [7, 8, 9],
 [8, 9, 10],
 [9, 10, 11],
 [10, 11],
 [11],
 [11, 12],
 [11, 12, 13],
 [12, 13, 14],
 [13, 14, 15],
 [14, 15, 16],
 [15, 16, 17],
 [16, 17],
 [17],
 [17, 18],
 [17, 18, 19],
 [18, 19, 20],
 [19, 20, 21],
 [20, 21, 22],
 [21, 22, 23],
 [22, 23],
 [23]]


In [87]:
def create_current_indexer(square_length):
    yield [None]
    n = 0
    while True:
        if n > 0 and (n+1) % (square_length/4) == 0:
            yield [n-1, n]
        else:
            yield [n]
        n += 1

def find_current_connecting_indices(square_length):
    indexer = create_current_indexer(square_length)
    all_indices = [ next(indexer) for _ in range(square_length) ]
    all_indices[-2].append(0)
    all_indices[-1].append(0)
    return all_indices

print(find_current_connecting_indices(8))

[[None], [0], [0, 1], [2], [2, 3], [4], [4, 5, 0], [6, 0]]


In [99]:
from pprint import pprint

def solve(threshold):
    inner_circle = [1]
    current_circle = []
    current_len = 8
    stop = False
    
    while not stop:       
        indices = zip(
            find_inner_connecting_indices(current_len),
            find_current_connecting_indices(current_len)
        )
        
        for inner, current in indices:
            print(inner)
            print(current)
            
            n = sum([ inner_circle[i] for i in inner]) + sum([ current_circle[i] for i in current if i != None])
            
            print(n)
            if (n > threshold):
                print("FOUND IT", n)
                stop = True
                return
            
            #print("=>", n, "\n")
            current_circle.append(n)
            print("=>", inner_circle)
            print("=>", current_circle, "\n")
        
        #pprint(current_circle)
        
        inner_circle = current_circle
        current_circle = []
        current_len += 8
        
    return -1
    
solve(289326)

[0]
[None]
1
=> [1]
=> [1] 

[0]
[0]
2
=> [1]
=> [1, 2] 

[0]
[0, 1]
4
=> [1]
=> [1, 2, 4] 

[0]
[2]
5
=> [1]
=> [1, 2, 4, 5] 

[0]
[2, 3]
10
=> [1]
=> [1, 2, 4, 5, 10] 

[0]
[4]
11
=> [1]
=> [1, 2, 4, 5, 10, 11] 

[0]
[4, 5, 0]
23
=> [1]
=> [1, 2, 4, 5, 10, 11, 23] 

[0]
[6, 0]
25
=> [1]
=> [1, 2, 4, 5, 10, 11, 23, 25] 

[7, 0]
[None]
26
=> [1, 2, 4, 5, 10, 11, 23, 25]
=> [26] 

[7, 0, 1]
[0]
54
=> [1, 2, 4, 5, 10, 11, 23, 25]
=> [26, 54] 

[0, 1]
[1]
57
=> [1, 2, 4, 5, 10, 11, 23, 25]
=> [26, 54, 57] 

[1]
[2]
59
=> [1, 2, 4, 5, 10, 11, 23, 25]
=> [26, 54, 57, 59] 

[1, 2]
[2, 3]
122
=> [1, 2, 4, 5, 10, 11, 23, 25]
=> [26, 54, 57, 59, 122] 

[1, 2, 3]
[4]
133
=> [1, 2, 4, 5, 10, 11, 23, 25]
=> [26, 54, 57, 59, 122, 133] 

[2, 3]
[5]
142
=> [1, 2, 4, 5, 10, 11, 23, 25]
=> [26, 54, 57, 59, 122, 133, 142] 

[3]
[6]
147
=> [1, 2, 4, 5, 10, 11, 23, 25]
=> [26, 54, 57, 59, 122, 133, 142, 147] 

[3, 4]
[6, 7]
304
=> [1, 2, 4, 5, 10, 11, 23, 25]
=> [26, 54, 57, 59, 122, 133, 142, 147, 304] 
